

# 効率的な最適化アルゴリズム

Optuna はハイパーパラメータのサンプリングと有望でないトライアルの
効率的な剪定に最新のアルゴリズムを採用することで、効率的なハイパーパラメータ最適化を実現します。

## サンプリングアルゴリズム

サンプラーは基本的に、提案されたパラメータ値と評価された目的値の記録を用いて
探索空間を継続的に絞り込んでいき、より良い目的値をもたらすパラメータを
導く最適な探索空間へと導きます。サンプラーがパラメータを提案する仕組みの詳細は
:class:`~optuna.samplers.BaseSampler` を参照してください。

Optuna では以下のサンプリングアルゴリズムを提供しています:

- :class:`~optuna.samplers.GridSampler` で実装されたグリッドサーチ

- :class:`~optuna.samplers.RandomSampler` で実装されたランダムサーチ

- :class:`~optuna.samplers.TPESampler` で実装されたツリー構造化パーゼン推定器 (TPE) アルゴリズム

- :class:`~optuna.samplers.CmaEsSampler` で実装された CMA-ES ベースのアルゴリズム

- :class:`~optuna.samplers.GPSampler` で実装されたガウス過程ベースのアルゴリズム

- 部分的に固定されたパラメータを可能にするアルゴリズムを実装した :class:`~optuna.samplers.PartialFixedSampler`

- :class:`~optuna.samplers.NSGAIISampler` で実装された非支配ソート遺伝的アルゴリズム II (NSGA-II)

- :class:`~optuna.samplers.QMCSampler` で実装された準モンテカルロサンプリングアルゴリズム

デフォルトのサンプラーは :class:`~optuna.samplers.TPESampler` です。

## サンプラーの切り替え


In [ ]:
import optuna

デフォルトでは、Optuna は :class:`~optuna.samplers.TPESampler` を以下のように使用します:



In [ ]:
study = optuna.create_study()
print(f"Sampler is {study.sampler.__class__.__name__}")

例えば :class:`~optuna.samplers.RandomSampler` や :class:`~optuna.samplers.CmaEsSampler` など
異なるサンプラーを使用したい場合:



In [ ]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler())
print(f"Sampler is {study.sampler.__class__.__name__}")

study = optuna.create_study(sampler=optuna.samplers.CmaEsSampler())
print(f"Sampler is {study.sampler.__class__.__name__}")

## プルーニングアルゴリズム

``Pruners`` はトレーニングの初期段階で見込みのないトライアルを自動的に停止します (自動早期停止)。
現在 :mod:`~optuna.pruners` モジュールは単一目的最適化でのみ使用されることを想定しています。

Optuna は以下のプルーニングアルゴリズムを提供します:

- :class:`~optuna.pruners.MedianPruner` で実装された中央値プルーニングアルゴリズム

- :class:`~optuna.pruners.NopPruner` で実装された非プルーニングアルゴリズム

- :class:`~optuna.pruners.PatientPruner` で実装された許容値付きプルーニングアルゴリズム

- :class:`~optuna.pruners.PercentilePruner` で実装されたトライアルの指定パーセンタイルをプルーニングするアルゴリズム

- :class:`~optuna.pruners.SuccessiveHalvingPruner` で実装された非同期逐次半減アルゴリズム

- :class:`~optuna.pruners.HyperbandPruner` で実装された Hyperband アルゴリズム

- :class:`~optuna.pruners.ThresholdPruner` で実装された閾値プルーニングアルゴリズム

- :class:`~optuna.pruners.WilcoxonPruner` で実装された [Wilcoxon 符号付き順位検定](https://en.wikipedia.org/wiki/Wilcoxon_signed-rank_test)_ に基づくプルーニングアルゴリズム

ほとんどの例では :class:`~optuna.pruners.MedianPruner` を使用しますが、
基本的には :class:`~optuna.pruners.SuccessiveHalvingPruner` や
:class:`~optuna.pruners.HyperbandPruner` の方が優れています ([このベンチマーク結果](https://github.com/optuna/optuna/wiki/Benchmarks-with-Kurobako)_ 参照)。


## プルーナーの有効化
プルーニング機能を有効にするには、反復トレーニングの各ステップ後に
:func:`~optuna.trial.Trial.report` と :func:`~optuna.trial.Trial.should_prune` を呼び出す必要があります。
:func:`~optuna.trial.Trial.report` は中間の目的値を定期的に監視します。
:func:`~optuna.trial.Trial.should_prune` は事前定義された条件を満たさないトライアルの終了を決定します。

主要な機械学習フレームワーク向けの統合モジュールの使用を推奨します。
専用リストは :mod:`~optuna.integration` で、使用例は [optuna-examples](https://github.com/optuna/optuna-examples/)_ で確認できます。



In [ ]:
import logging
import sys

import sklearn.datasets
import sklearn.linear_model
import sklearn.model_selection


def objective(trial):
    iris = sklearn.datasets.load_iris()
    classes = list(set(iris.target))
    train_x, valid_x, train_y, valid_y = sklearn.model_selection.train_test_split(
        iris.data, iris.target, test_size=0.25, random_state=0
    )

    alpha = trial.suggest_float("alpha", 1e-5, 1e-1, log=True)
    clf = sklearn.linear_model.SGDClassifier(alpha=alpha)

    for step in range(100):
        clf.partial_fit(train_x, train_y, classes=classes)

        # 中間の目的関数値を報告
        intermediate_value = 1.0 - clf.score(valid_x, valid_y)
        trial.report(intermediate_value, step)

        # 中間値に基づくプルーニング処理
        if trial.should_prune():
            raise optuna.TrialPruned()

    return 1.0 - clf.score(valid_x, valid_y)

プルーニング条件として中央値停止ルールを設定



In [ ]:
# メッセージ表示用のストリームハンドラを追加
optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study = optuna.create_study(pruner=optuna.pruners.MedianPruner())
study.optimize(objective, n_trials=20)

ご覧の通り、いくつかのトライアルは全イテレーションを完了する前にプルーニング（停止）されました。
メッセージの形式は ``"Trial <トライアル番号> pruned."`` です。



## どのサンプラーとプルーナーを使用するべきか？

[optuna/optuna - wiki "Benchmarks with Kurobako"](https://github.com/optuna/optuna/wiki/Benchmarks-with-Kurobako)_ で公開されているベンチマーク結果によると、少なくとも深層学習以外のタスクでは、

* :class:`~optuna.samplers.RandomSampler` には :class:`~optuna.pruners.MedianPruner` が最適です。
* :class:`~optuna.samplers.TPESampler` には :class:`~optuna.pruners.HyperbandPruner` が最適です。

ただし、このベンチマークは深層学習タスクを対象としていない点にご注意ください。
深層学習タスクについては、以下の表を参照してください。
この表は [Ozaki et al., Hyperparameter Optimization Methods: Overview and Characteristics, in IEICE Trans, Vol.J103-D No.9 pp.615-631, 2020](https://doi.org/10.14923/transinfj.2019JDR0003)_ 論文（日本語）に基づいています。

+---------------------------+-----------------------------------------+---------------------------------------------------------------+
| 並列計算リソース          | カテゴリカル/条件付きハイパーパラメータ | 推奨アルゴリズム                                              |
+===========================+=========================================+===============================================================+
| 制限あり                  | なし                                    | TPE. 探索空間が低次元かつ連続的なら GP-EI                     |
+                           +-----------------------------------------+---------------------------------------------------------------+
|                           | あり                                    | TPE. 探索空間が低次元かつ連続的なら GP-EI                     |
+---------------------------+-----------------------------------------+---------------------------------------------------------------+
| 十分                      | なし                                    | CMA-ES, ランダムサーチ                                        |
+                           +-----------------------------------------+---------------------------------------------------------------+
|                           | あり                                    | ランダムサーチまたは遺伝的アルゴリズム                        |
+---------------------------+-----------------------------------------+---------------------------------------------------------------+




## プルーニング用統合モジュール
Optuna では、プルーニング機構をより簡潔に実装するため、以下のライブラリ向けの統合モジュールを提供しています。

Optuna の統合モジュールの完全な一覧は :mod:`~optuna.integration` を参照してください。

例えば、[LightGBMPruningCallback](https://optuna-integration.readthedocs.io/en/stable/reference/generated/optuna_integration.LightGBMPruningCallback.html)_ は、学習イテレーションのロジックを直接変更することなくプルーニングを導入します。
(完全なスクリプトについては [example](https://github.com/optuna/optuna-examples/blob/main/lightgbm/lightgbm_integration.py)_ も参照してください)

```text
import optuna.integration

pruning_callback = optuna.integration.LightGBMPruningCallback(trial, 'validation-error')
gbm = lgb.train(param, dtrain, valid_sets=[dvalid], callbacks=[pruning_callback])
```
